In [1170]:
import torch
import gpytorch
import numpy as np
import pandas as pd
import itertools
import random
import pickle
import math
import cv2
import os
import re
from torch.nn.utils import clip_grad_norm_
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from mpl_toolkits.mplot3d import Axes3D  # Import 3D plotting toolkit
from numpy.linalg import inv
from gpytorch.likelihoods import MultitaskGaussianLikelihood

In [1171]:
#Load data and prepare it for the GP
data = pd.read_csv('bf_sph_sound_0.csv')  

x_column = data['x_distance'].values
y_column = data['y_distance'].values
sound_intensity_column = data['sound_intensity'].values
direction = data['direction'].values #tan theta values

normalized_angles = np.column_stack((np.sin(direction), np.cos(direction)))
normalized_angles = [[float(str(val).replace(' ', '')) for val in row] for row in normalized_angles]
#print(normalized_angles)

min_numeric_value = np.nanmin(sound_intensity_column)
max_numeric_value = np.nanmax(sound_intensity_column[np.isfinite(sound_intensity_column)])

sound_intensity_column[np.isnan(sound_intensity_column)] = min_numeric_value 
sound_intensity_column[np.isinf(sound_intensity_column)] = max_numeric_value

#Normalise sound intensity values
mean_SIL_true = np.mean(sound_intensity_column, axis=0)
std_SIL_true = np.std(sound_intensity_column, axis=0)

sound_intensity_column = (sound_intensity_column - mean_SIL_true) / std_SIL_true

true_Y = np.column_stack([sound_intensity_column, normalized_angles])
#print(true_Y)

intensity_loss_2d = sound_intensity_column.reshape(101, 101)

corner_coordinates = [[-50.,-50.], [50.,50.], [-50.,50.], [50.,-50.]]
corner_coordinates_tensor = torch.tensor(corner_coordinates)

all_coordinates = list(zip(x_column,y_column))
all_coordinates = np.array(all_coordinates)
all_coordinates = [[float(str(val).replace(' ', '')) for val in row] for row in all_coordinates]
all_coordinates_tensor = torch.tensor(all_coordinates)

In [1172]:
###Defining initial variables 

sampled_data = []
coordinates_passed = []
sampled_y =[]
sound_intensity_sampled = []
sound_y = []

sigma = 0.02

start_location = [48.0, 48.0] #define start location of the robot

n_samples = len(sound_intensity_column)
distance_horizon = 3  # Set your desired distance horizon
prediction_horizon = 3  # Set your desired prediction horizon
training_iter = 75  # Set your desired number of iterations
initial_sample_size = 8 # Set your desired initial training set size

x_test_global = np.array(all_coordinates)
x_test_local = []

sample_iter = math.floor(n_samples/3)#int(200)
var_iter = []
var_iter_local = []
var_iter_global = []
rmse_local_true = []
rmse_global_true = []
#covar_global = []
covar_trace = []
covar_totelements = []
covar_nonzeroelements = []


noise = []
lengthscale = []

AIC = [] # Akaike Information Criterion
BIC = [] # Bayesian Information Criterion

f2_H_global = []
f2_H_local = []

image_path = 'D:\\UHM ORE\\Active Leanring\\scripts\\images\\'

x_max = [0., 0.] #Point with maximum global uncertainity
#Intialise Plot
fig = plt.figure(figsize=(24, 16))

<Figure size 2400x1600 with 0 Axes>

In [1173]:
class MultiTaskGPModel(gpytorch.models.ExactGP):
    def __init__(self, train_x, train_y, likelihood):
        super(MultiTaskGPModel, self).__init__(train_x, train_y, likelihood)
        self.mean_module =  gpytorch.means.MultitaskMean(
            gpytorch.means.ConstantMean(), num_tasks=3
        )
        self.covar_module = gpytorch.kernels.MultitaskKernel(
            gpytorch.kernels.RBFKernel(), num_tasks=3, rank=1
        )

    def forward(self, x):
        mean_x = self.mean_module(x)
        covar_x = self.covar_module(x)
        return gpytorch.distributions.MultitaskMultivariateNormal(mean_x, covar_x)

In [1174]:
# def kernel_print(i, training_iter, loss, model):
#     print('Iter %d/%d - Loss: %.3f   lengthscale: %.3f %.3f   noise: %.3f' % (
#             i + 1, training_iter, loss.item(),
#             model.covar_module.base_kernel.lengthscale.detach().numpy()[0][0],
#             model.covar_module.base_kernel.lengthscale.detach().numpy()[0][1],
#             model.likelihood.noise.detach().numpy()
#         ))

In [1175]:
def GPtrain(x_train, y_train, training_iter):
    
    # initialize likelihood and model
    likelihood = MultitaskGaussianLikelihood(num_tasks=3)
    model = MultiTaskGPModel(x_train, y_train, likelihood)
    # Find optimal model hyperparameters
    model.train()
    likelihood.train()
    
    # Use the adam optimizer
    optimizer = torch.optim.Adam([
        {'params': model.parameters()},  # Includes GaussianLikelihood parameters
    ], lr=0.1)
    
    # "Loss" for GPs - the marginal log likelihood
    mll = gpytorch.mlls.ExactMarginalLogLikelihood(likelihood, model)

    # train GP model
    for i in range(training_iter):
        optimizer.zero_grad()
        output = model(x_train)
        loss = -mll(output, y_train)
        loss.backward()
        #kernel_print(i, training_iter, loss, model)
        print('Iter %d/%d - Loss: %.3f' % (i + 1, training_iter, loss.item()))
        optimizer.step()
    
    return likelihood, model, optimizer, output, loss

In [1176]:
def GPEval(x_test, model, likelihood):
    model.eval()
    likelihood.eval()
    
    # Make predictions by feeding model through likelihood
    with torch.no_grad(), gpytorch.settings.fast_pred_var():
        predictions = likelihood(model(x_test))
        mean = predictions.mean
        lower, upper = predictions.confidence_region()
        variance = upper.numpy() - lower.numpy()
    return mean.numpy(), variance, lower.numpy(), upper.numpy()

In [1177]:
def paramValue(x, y):
    x = x.item()
    y = y.item()
    #print(type(x))
    index = np.where((x_column == x) & (y_column == y))[0]

    if index:
        corresponding_intensity = sound_intensity_column[index[0]]
        corresponding_angle = normalized_angles[index[0]]
        #print(f"Sound intensity at ({x}, {y}): {corresponding_intensity}")
    else:
        print(f"No data found for ({x}, {y})")
        corresponding_intensity = 0.0
        corresponding_angle = [0, 0]

    return corresponding_intensity, corresponding_angle

In [1178]:
#x_true is all_points, #i_Sample is current coordinate, i_train = coordinates_passed
def plotGP():
    ax1 = fig.add_subplot(4, 3, 1, projection='3d')
    #ax1.set_xlim(-60, 60)
    #ax1.set_ylim(-60, 60)
    #ax1.set_zlim(sound_intensity_column.min(), sound_intensity_column.max())
    ax1.set_xlabel('X Coordinate')
    ax1.set_ylabel('Y Coordinate')
    ax1.set_zlabel('sound intensity')
    ax1.view_init(20, 20)
    ax1.set_title('asv on surface '+str(coordinates_passed[-1]))
    x_distances = np.arange(-50, 51, 1).astype(float)
    y_distances = np.arange(-50, 51, 1).astype(float)
    X, Y = np.meshgrid(x_distances, y_distances)
    ax1.plot_surface(X, Y, intensity_loss_2d, cmap='viridis', alpha=0.7)

    

    asv_path = ax1.plot3D([coord[0] for coord in coordinates_passed], [coord[1] for coord in coordinates_passed], sound_intensity_sampled, color='black')
    asv = ax1.scatter3D(coordinates_passed[-1][0], coordinates_passed[-1][1], 
                        sound_intensity_sampled[-1], s=100, color='black', marker='*', zorder=1)
    # # color by LAMP
    # surf = ax1.plot_trisurf(x_true[:, 0], x_true[:, 1], y_obs, cmap='inferno',
    #                         linewidth=0, alpha=0.25, vmax=max(y_obs), vmin=min(y_obs))
    points_pred = ax1.plot_trisurf(
         x_test_global[:, 0], x_test_global[:, 1], f_mean_global[:, 0], color='grey', alpha=0.25)
    # # Shade between the lower and upper confidence bounds
    for i_test in range(len(x_test_local)):
        ax1.plot(x_test_local[i_test][0].numpy()*np.array([1, 1]), x_test_local[i_test][1].numpy()*np.array([1, 1]), 
                 np.array([lower_local[i_test], upper_local[i_test]]), 'gray')

 
    #AX2 is diff
    ax2 = fig.add_subplot(4, 3, 2)
    ax2.set_xlim(-60,60)
    ax2.set_ylim(-60,60)
    ax2.set_xlabel('x coordinate')
    ax2.set_ylabel('y coordinate')
    ax2.set_title('asv on surface ' + str(coordinates_passed[-1]))
    contour = ax2.contourf(X, Y, intensity_loss_2d, cmap='viridis')
    cbar = fig.colorbar(contour)
    cbar.set_label('Sound Intensity')
    asv_path = ax2.plot([coord[0] for coord in coordinates_passed], [coord[1] for coord in coordinates_passed], color='pink')
    asv = ax2.scatter(coordinates_passed[-1][0], coordinates_passed[-1][1], color='pink', marker='*', label='ASV', s=100)
    ax2.scatter(x_max[0], x_max[1], color='red', label='global maximum uncertainity', s=50)



    ax3 = fig.add_subplot(4, 3, 3)
    ax3.plot(range(0, len(var_iter_local)),
             var_iter_local, color='blue', marker='.')
    ax3.plot(range(0, len(var_iter_global)),
             var_iter_global, color='black', marker='*')
    ax3.set_xlabel('number of samples')
    ax3.set_title('variance of samples')
    ax3.legend(['local', 'global'], loc='upper right')


    
    ax4 = fig.add_subplot(4, 3, 4)
    local_rms = ax4.plot(range(0, len(rmse_local_true)),
                         rmse_local_true, color='blue', marker='.', label='local')
    global_rms = ax4.plot(range(0, len(rmse_global_true)),
                          rmse_global_true, color='black', marker='*', label='global')
    ax4.set_xlabel('number of samples')
    ax4.legend(['local', 'global'], loc='upper right')
    ax4.set_title('rmse of learned model')
    
    ax5 = fig.add_subplot(4, 3, 5)
    ax6 = fig.add_subplot(4, 3, 6)

    # lengthscale_arr = np.array(lengthscale)
    # length0_plot = ax5.plot(range(0, len(lengthscale)),
    #                      lengthscale_arr[:,0], color='mediumpurple', marker='.', label='lengthscale')
    # length1_plot = ax5.plot(range(0, len(lengthscale)),
    #                      lengthscale_arr[:,1], color='rebeccapurple', marker='.', label='lengthscale')
    # ax5.set_ylim([0, np.max(lengthscale_arr)*1.1])
    # noise_plot = ax6.plot(range(0, len(noise)),
    #                      noise, color='teal', marker='.', label='noise')
    # ax5.set_xlabel('number of samples')
    # ax5.set_ylabel('lengthscale',color='mediumpurple')
    ax6.set_ylabel('noise',color='teal')
    ax6.set_xlabel('number of samples')

    

    #Changing trace plot 
    
    ax7 = fig.add_subplot(4, 3, 7)
    tot_elements = ax7.plot(range(0, len(covar_totelements)),
                         covar_totelements, color='mediumvioletred', marker='.', label='total_elements')
    nonzero_elements = ax7.plot(range(0, len(covar_nonzeroelements)),
                         covar_nonzeroelements, color='blue', marker='.', label='nonzero_elements')
    ax7.set_ylabel('elements')
    ax7.set_xlabel('number of samples')
    ax7.legend(['total', 'nonzero'], loc='lower right')
    
    ax8 = fig.add_subplot(4, 3, 8)
    AIC_plot = ax8.plot(range(0, len(AIC)), AIC, color='blue', marker='.', label='AIC')
    BIC_plot = ax8.plot(range(0, len(BIC)), BIC, color='black', marker='*', label='BIC')
    ax8.set_xlabel('number of samples')
    ax8.legend(['AIC', 'BIC'], loc='lower right')
    ax8.set_ylabel('information criteria of learned model')
    
    ax9 = fig.add_subplot(4, 3, 9)
    RKHS_local_plot = ax9.plot(range(0, len(f2_H_local)), f2_H_local, color='blue', marker='.', label='f^2_H')
    RKHS_global_plot = ax9.plot(range(0, len(f2_H_global)), f2_H_global, color='black', marker='.', label='f^2_H')
    ax9.set_ylabel('RKHS_norm')
    ax9.set_xlabel('number of samples')
    ax8.legend(['local', 'global'], loc='lower right')

    ax10 = fig.add_subplot(4, 3, 10)
    trace = ax10.plot(range(0, len(covar_trace)),
                         covar_trace, color='pink', marker='.', label='trace')
    ax10.set_xlabel('number of samples')
    ax10.set_ylabel('trace',color='pink')

    x_grid_global = all_coordinates_tensor[:, 0].numpy()
    y_grid_global = all_coordinates_tensor[:, 1].numpy()
    x_grid_local = all_new_locations[:, 0].numpy()
    y_grid_local = all_new_locations[:, 1].numpy()
    # ax11 = fig.add_subplot(4, 3, 11)
    # ax12 = fig.add_subplot(4, 3, 12)
    # contour_global = ax11.scatter(x_grid_global, y_grid_global, c=MI_local, cmap='viridis')
    # contour_local = ax12.scatter(x_grid_global, y_grid_global, c=f_var_global, cmap='viridis')
    # cbar_global = fig.colorbar(contour_global)
    # cbar_global.set_label('Sampling Strategy Parameter')
    # cbar_local = fig.colorbar(contour_local)
    # cbar_local.set_label('Sampling Strategy Parameter')
    # ax11.set_xlabel('x coordinate global')
    # ax12.set_xlabel('x coordinate local')
    # ax11.set_ylabel('y coordinate global')
    # ax12.set_ylabel('y coordinate local')
    # ax11.set_title('Global MI Contour Map')
    # ax12.set_title('Global Varience Contour Map')

    return ax1, ax2, ax3, ax4, ax5, ax6, ax7, ax8, ax9, ax10, 
# ax11, ax12

In [1179]:
def PotentialNeighbors(current_coordinate, potential_neighbors, coordinates_passed):
    filtered = []
    # Traverse to a random nearest neighbor location
    for n in potential_neighbors:
        coordinate = current_coordinate+n
        arr_coord = coordinate.tolist()
        #print(arr_coord)
        #print(coordinates_passed)
        if arr_coord not in corner_coordinates:
            if arr_coord in all_coordinates:
                if arr_coord not in coordinates_passed:
                    filtered.append(coordinate.tolist())

    return filtered


In [1180]:
def CheckConvergence():
    v = rmse_global_true
    vo = np.max(rmse_global_true)
    vfo = rmse_global_true[-1]

    dv = vo-vfo
    dv_2_percent = 0.02*dv

    # Is there even enough data to confirm convergence?
    v_95thresh = vo - 0.95*dv
    i_95thresh = np.where(v < v_95thresh)
    i_95thresh = np.array(i_95thresh[0], dtype=int)
    if len(i_95thresh) >= 10:
        for i in range(len(i_95thresh)):
            v_con = v[i_95thresh[i]:-1]
            vf = np.mean(v_con)

In [1181]:
def SamplingMuAndVar(var, mean, potential_neighbors):
    alpha = 10
    beta = 1
    sampling_mu_var = beta*mean+alpha*var
    sampling_mu_var_max = np.nanmax(sampling_mu_var)
    sampling_mu_var_max = np.where(sampling_mu_var == sampling_mu_var_max)[0]
    next_sample = potential_neighbors.numpy()[sampling_mu_var_max,:]
    # print(next_sample)
    next_sample = next_sample[0]
    return next_sample, sampling_mu_var

In [1182]:
# calculate RKHS norm from covariance
def RKHS_norm(y,sigma,K):
    n_row, n_col = K.shape
    alpha = inv(K + sigma**2 * np.eye(n_row)) @ y
    return alpha.transpose() @ K @ alpha

In [1183]:
#Defining neighbors based on distance horizon
coordinates_range = range(-distance_horizon, distance_horizon)
all_coordinate_combinations = list(itertools.product(coordinates_range, repeat=2))
potential_neighbors = torch.tensor(all_coordinate_combinations, dtype=torch.float32)

In [1184]:
#Random walk for initial training
initial_training_set = []

asv_start_location = torch.tensor(start_location, dtype=torch.float32)  # Start at center
asv_location = asv_start_location
for _ in range(initial_sample_size):
    x = asv_location
    spl, angle = paramValue(x[0], x[1])  # Sample sound intensity and direction at this location
    # print(spl)
    # print(angle)
    y = np.concatenate([[spl], angle])
    y = torch.tensor(y)
    spl =torch.tensor(spl)
    print(y)
    sound_intensity_sampled.append(spl)
    sampled_y.append(y)
    initial_training_set.append((x, y))
    coordinates_passed.append(x.tolist())

    filtered_neighbors = PotentialNeighbors(x, potential_neighbors, coordinates_passed)
    filtered_neighbors = torch.tensor(filtered_neighbors)
    new_location = random.choice(filtered_neighbors)
    asv_location = new_location
    #print(f"Moved to: {asv_location}")

tensor([-1.3005, -0.7071, -0.7071], dtype=torch.float64)
tensor([-1.2801, -0.6941, -0.7198], dtype=torch.float64)
tensor([-1.3609, -0.6950, -0.7190], dtype=torch.float64)
tensor([-1.3409, -0.7071, -0.7071], dtype=torch.float64)
tensor([-1.2171, -0.7071, -0.7071], dtype=torch.float64)
tensor([-1.1967, -0.7474, -0.6644], dtype=torch.float64)
tensor([-1.1740, -0.7071, -0.7071], dtype=torch.float64)
tensor([-1.2592, -0.7071, -0.7071], dtype=torch.float64)


In [1185]:
# Explore the surface
#training_set = initial_training_set.copy()
# print(initial_training_set)
# likelihood = MultitaskGaussianLikelihood(num_tasks=y_train.size(-1))

In [1186]:
for k in range(sample_iter):
    # Train Gaussian Process Model
    X_train, y_train = zip(*initial_training_set)
    print(X_train)
    print(y_train)
    X_train = torch.stack(X_train)
    y_train = torch.stack(y_train)

    X_train = X_train.float()
    y_train = y_train.float()

    likelihood, model, optimizer, output, loss = GPtrain(X_train, y_train, training_iter)

    noise.append(model.likelihood.noise.detach().numpy())
    #lengthscale.append(model.covar_module.multi_task_kernel.lengthscale.detach().numpy()[0])

    model.eval()
    likelihood.eval()

    all_new_locations = PotentialNeighbors(asv_location, potential_neighbors, coordinates_passed)
    all_new_locations = torch.tensor(all_new_locations) #This is my x_test_local
    x_test_local = all_new_locations
    

    SIL_test_true = [] #SIL is Sound INtensity Level
    for i in all_new_locations:
        spl, angle = paramValue(i[0], i[1])
        sil = np.concatenate([[spl], angle])
        SIL_test_true.append(sil)

    #Local
    f_mean_local, f_var_local, lower_local_all, upper_local_all,   = GPEval(all_new_locations, model, likelihood)
    lower_local = lower_local_all[:, 0]
    upper_local = upper_local_all[:, 0]
    # print(lower_local_all)
    # print(lower_local)
    mse_local_true = mean_squared_error(SIL_test_true, f_mean_local)
    rmse_local_true.append(math.sqrt(mse_local_true))

    #global
    f_mean_global, f_var_global, lower_global, upper_global,  = GPEval(all_coordinates_tensor, model, likelihood)
    #print(f_mean_global)
    mse_global_true = mean_squared_error(true_Y, f_mean_global)
    rmse_global_true.append(math.sqrt(mse_global_true))

    if var_iter_local:
        next_sample, sampling_mu_var = SamplingMuAndVar(f_var_local[:, 0], f_mean_local[:, 0], all_new_locations) # checkiong within potential neighbors
        
    else:
        next_sample = np.nanmax(f_var_local)
        next_sample = np.where(f_var_local == next_sample)[0]
        next_sample = all_new_locations.numpy()[next_sample,:]

        distances = np.linalg.norm(asv_location - next_sample, axis=1)
        closest_index = np.argmin(distances)
        closest_point = next_sample[closest_index]
        next_sample = closest_point

    print(next_sample)
    var_iter_global.append(max(f_var_global[:, 1]))
    var_iter_local.append(max(f_var_local[:, 1]))

    #covar_global.append(f_covar_global)
    covar_trace.append(np.trace(f_var_global))
    covar_totelements.append(np.size(f_var_global))
    covar_nonzeroelements.append(np.count_nonzero(f_var_global))
    mll = gpytorch.mlls.ExactMarginalLogLikelihood(likelihood, model)

    # now evaluate information criteria
    # akaike information criterion
    AIC_sample = 2*np.log(covar_nonzeroelements[-1]) - 2*np.log(mse_global_true)
    AIC.append(AIC_sample)
    # BIC calculated from https://en.wikipedia.org/wiki/Bayesian_information_criterion#Gaussian_special_case
    BIC_sample = np.size(coordinates_passed)*np.log(covar_nonzeroelements[-1]) - 2*np.log(mse_global_true)
    BIC.append(BIC_sample)
    
    # and finally evaluate RKHS norm
    # K_global = output._covar.detach().numpy()
    # print(K_global)
    # y_global = y_train.numpy().reshape(len(y_global),3)
    # # y_global = y_global[:, 1]
    # # y_glonal = y_global.reshape(len(y_global),3)
    # print(y_global)
    # f2_H_sample = RKHS_norm(y_global,sigma,K_global)
    # f2_H_global.append(f2_H_sample[0,0])
    
    # n_set = len(initial_training_set)
    # n_sub = math.floor(n_set/2)
    # i_sub = random.sample(range(1,n_set),n_sub)
    # i_sub.sort()
    # K_local = K_global[np.ix_(i_sub,i_sub)]
    # y_local = y_global[i_sub]
    # f2_H_sample = RKHS_norm(y_local,sigma,K_local)
    # f2_H_local.append(f2_H_sample[0,0])
    
    # plot real surface and the observed measurements
    # print(lengthscale)
    ax1, ax2, ax3, ax4, ax5, ax6, ax7, ax8, ax9, ax10 = plotGP() #, ax11, ax12
    plt.show()

    fig.tight_layout()
    fig.savefig(image_path+str(len(set(initial_training_set)))+'.png')
    fig.clear()
    
    prev_var_pred_global = f_var_global
    prev_var_pred_local = f_var_local
    
    x_max = next_sample
    asv_location = torch.tensor(next_sample)
    coordinates_passed.append(asv_location.tolist())

    new_spl, new_angle = paramValue(asv_location[0], asv_location[1])
    new_y = np.concatenate([[new_spl], new_angle])
    new_y = torch.tensor(new_y)
    sampled_y.append(new_y)
    sound_intensity_sampled.append(spl)
    sampled_data.append((new_location[0], new_location[1], new_y))
    new_data_point = (asv_location, new_y)
    print(new_data_point)
    initial_training_set.append(new_data_point)


(tensor([48., 48.]), tensor([48., 47.]), tensor([50., 49.]), tensor([49., 49.]), tensor([46., 46.]), tensor([44., 47.]), tensor([45., 45.]), tensor([47., 47.]))
(tensor([-1.3005, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2801, -0.6941, -0.7198], dtype=torch.float64), tensor([-1.3609, -0.6950, -0.7190], dtype=torch.float64), tensor([-1.3409, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2171, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.1967, -0.7474, -0.6644], dtype=torch.float64), tensor([-1.1740, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2592, -0.7071, -0.7071], dtype=torch.float64))
Iter 1/75 - Loss: 1.550
Iter 2/75 - Loss: 1.470
Iter 3/75 - Loss: 1.394
Iter 4/75 - Loss: 1.323
Iter 5/75 - Loss: 1.258
Iter 6/75 - Loss: 1.195
Iter 7/75 - Loss: 1.135
Iter 8/75 - Loss: 1.075
Iter 9/75 - Loss: 1.016
Iter 10/75 - Loss: 0.957
Iter 11/75 - Loss: 0.897
Iter 12/75 - Loss: 0.837
Iter 13/75 - Loss: 0.779
Iter 14/75 - Loss: 0.724
Iter 15/75 - Loss: 0.674
Iter 16/

C:\Users\prajn\AppData\Local\Temp\ipykernel_19816\242739269.py:101: UserWarning: The figure layout has changed to tight
  fig.tight_layout()


(tensor([45., 38.]), tensor([-1.0223, -0.5843, -0.8115], dtype=torch.float64))
(tensor([48., 48.]), tensor([48., 47.]), tensor([50., 49.]), tensor([49., 49.]), tensor([46., 46.]), tensor([44., 47.]), tensor([45., 45.]), tensor([47., 47.]), tensor([48., 41.]), tensor([45., 38.]))
(tensor([-1.3005, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2801, -0.6941, -0.7198], dtype=torch.float64), tensor([-1.3609, -0.6950, -0.7190], dtype=torch.float64), tensor([-1.3409, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2171, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.1967, -0.7474, -0.6644], dtype=torch.float64), tensor([-1.1740, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2592, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.1582, -0.6000, -0.8000], dtype=torch.float64), tensor([-1.0223, -0.5843, -0.8115], dtype=torch.float64))
Iter 1/75 - Loss: 1.520
Iter 2/75 - Loss: 1.451
Iter 3/75 - Loss: 1.382
Iter 4/75 - Loss: 1.313
Iter 5/75 - Loss: 1.245
Iter 6/75 - Loss: 1

C:\Users\prajn\AppData\Local\Temp\ipykernel_19816\242739269.py:101: UserWarning: The figure layout has changed to tight
  fig.tight_layout()


(tensor([42., 35.]), tensor([-0.8764, -0.5633, -0.8262], dtype=torch.float64))
(tensor([48., 48.]), tensor([48., 47.]), tensor([50., 49.]), tensor([49., 49.]), tensor([46., 46.]), tensor([44., 47.]), tensor([45., 45.]), tensor([47., 47.]), tensor([48., 41.]), tensor([45., 38.]), tensor([42., 35.]))
(tensor([-1.3005, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2801, -0.6941, -0.7198], dtype=torch.float64), tensor([-1.3609, -0.6950, -0.7190], dtype=torch.float64), tensor([-1.3409, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2171, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.1967, -0.7474, -0.6644], dtype=torch.float64), tensor([-1.1740, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.2592, -0.7071, -0.7071], dtype=torch.float64), tensor([-1.1582, -0.6000, -0.8000], dtype=torch.float64), tensor([-1.0223, -0.5843, -0.8115], dtype=torch.float64), tensor([-0.8764, -0.5633, -0.8262], dtype=torch.float64))
Iter 1/75 - Loss: 1.703
Iter 2/75 - Loss: 1.634
Iter 3/75 - L

...

C:\Users\prajn\AppData\Local\Temp\ipykernel_19816\242739269.py:101: UserWarning: The figure layout has changed to tight
  fig.tight_layout()


(tensor([2., 4.]), tensor([4.0287, 0.6644, 0.7474], dtype=torch.float64))
(tensor([48., 48.]), tensor([48., 47.]), tensor([50., 49.]), tensor([49., 49.]), tensor([46., 46.]), tensor([44., 47.]), tensor([45., 45.]), tensor([47., 47.]), tensor([48., 41.]), tensor([45., 38.]), tensor([42., 35.]), tensor([44., 32.]), tensor([41., 29.]), tensor([38., 26.]), tensor([40., 23.]), tensor([37., 20.]), tensor([34., 17.]), tensor([36., 14.]), tensor([33., 11.]), tensor([30.,  8.]), tensor([32.,  5.]), tensor([29.,  2.]), tensor([26., -1.]), tensor([28., -4.]), tensor([25., -7.]), tensor([ 22., -10.]), tensor([ 24., -13.]), tensor([ 21., -16.]), tensor([ 23., -19.]), tensor([ 20., -22.]), tensor([ 17., -25.]), tensor([ 19., -28.]), tensor([ 16., -31.]), tensor([ 13., -34.]), tensor([ 15., -37.]), tensor([ 12., -40.]), tensor([  9., -43.]), tensor([ 11., -46.]), tensor([  8., -49.]), tensor([  5., -47.]), tensor([  2., -50.]), tensor([ -1., -48.]), tensor([ -4., -50.]), tensor([ -7., -48.]), tensor(

C:\Users\prajn\AppData\Local\Temp\ipykernel_19816\242739269.py:101: UserWarning: The figure layout has changed to tight
  fig.tight_layout()


(tensor([3., 3.]), tensor([4.1320, 0.7071, 0.7071], dtype=torch.float64))
(tensor([48., 48.]), tensor([48., 47.]), tensor([50., 49.]), tensor([49., 49.]), tensor([46., 46.]), tensor([44., 47.]), tensor([45., 45.]), tensor([47., 47.]), tensor([48., 41.]), tensor([45., 38.]), tensor([42., 35.]), tensor([44., 32.]), tensor([41., 29.]), tensor([38., 26.]), tensor([40., 23.]), tensor([37., 20.]), tensor([34., 17.]), tensor([36., 14.]), tensor([33., 11.]), tensor([30.,  8.]), tensor([32.,  5.]), tensor([29.,  2.]), tensor([26., -1.]), tensor([28., -4.]), tensor([25., -7.]), tensor([ 22., -10.]), tensor([ 24., -13.]), tensor([ 21., -16.]), tensor([ 23., -19.]), tensor([ 20., -22.]), tensor([ 17., -25.]), tensor([ 19., -28.]), tensor([ 16., -31.]), tensor([ 13., -34.]), tensor([ 15., -37.]), tensor([ 12., -40.]), tensor([  9., -43.]), tensor([ 11., -46.]), tensor([  8., -49.]), tensor([  5., -47.]), tensor([  2., -50.]), tensor([ -1., -48.]), tensor([ -4., -50.]), tensor([ -7., -48.]), tensor(

KeyboardInterrupt: 

In [ ]:
# %% convert images to video

video_name = 'asv_motion_model.avi'

images = []
int_list = []
for img in os.listdir(image_path):
    if img.endswith(".png"):
        images.append(img)
        s = re.findall(r'\d+', img)
        try:
            int_list.append(int(s[0]))
        except:
            print("whatever")

arg_list = np.argsort(int_list)

frame = cv2.imread(os.path.join(image_path, images[0]))
height, width, layers = frame.shape

video = cv2.VideoWriter(
    video_name, cv2.VideoWriter_fourcc(*'DIVX'), 30, (width, height))

for i in range(len(arg_list)):
    image = images[arg_list[i]]
    video.write(cv2.imread(os.path.join(image_path, image)))

cv2.destroyAllWindows()
video.release()

In [ ]:
class data:
    def __init__(self, x_true, y_obs, i_train, var_iter_global, mse_global_true, 
                 rmse_global_true, mse_global_obs, rmse_global_obs, var_iter_local, 
                 mse_local_true, rmse_local_true, mse_local_obs, rmse_local_obs, 
                 x_test_local, x_test_global, covar_global, covar_trace, 
                 covar_totelements, covar_nonzeroelements, AIC, BIC, f2_H_local, f2_H_global):
        # likelihood, model, optimizer, output, loss,
        self.x_true = x_true
        self.y_obs = y_obs
        self.i_train = i_train
        # self.likelihood = likelihood
        # self.model = model
        # self.optimizer = optimizer
        # self.output = output
        # self.loss = loss
        self.var_iter_global = var_iter_global
        self.mse_global_true = mse_global_true
        self.rmse_global_true = rmse_global_true
        self.mse_global_obs = mse_global_obs
        self.rmse_global_obs = rmse_global_obs
        self.var_iter_local = var_iter_local
        self.mse_local_true = mse_local_true
        self.rmse_local_true = rmse_local_true
        self.mse_local_obs = mse_local_obs
        self.rmse_local_obs = rmse_local_obs
        self.x_test_local = x_test_local
        self.x_test_global = x_test_global
        self.covar_global = covar_global
        self.covar_trace = covar_trace
        self.covar_totelements = covar_totelements
        self.covar_nonzeroelements = covar_nonzeroelements
        self.AIC = AIC
        self.BIC = BIC
        self.f2_H_local = f2_H_local
        self.f2_H_global = f2_H_global


mydata = data(all_coordinates, sound_intensity_column, training_set, var_iter_global, mse_global_true, rmse_global_true, mse_global_true, rmse_global_true,
              var_iter_local, mse_local_true, rmse_local_true, mse_local_true, rmse_local_true, x_test_local, x_test_global,
              f_covar_global, covar_trace, covar_totelements, covar_nonzeroelements, AIC, BIC, f2_H_local, f2_H_global)
#likelihood, model, optimizer, output, loss,
with open("data.p", "wb") as f:
    pickle.dump(mydata, f)

In [ ]:
# %% load data script
with open("data.p", "rb") as f:
    mydata = pickle.load(f)
x_true = mydata.x_true
y_obs = mydata.y_obs
i_train = mydata.i_train
# likelihood = mydata.likelihood
# model = mydata.model
# optimizer = mydata.optimizer
# output = mydata.output
# loss = mydata.loss
var_iter_global = mydata.var_iter_global
mse_global_true = mydata.mse_global_true
rmse_global_true = mydata.rmse_global_true
mse_global_obs = mydata.mse_global_obs
rmse_global_obs = mydata.rmse_global_obs
var_iter_local = mydata.var_iter_local
mse_local_true = mydata.mse_local_true
rmse_local_true = mydata.rmse_local_true
mse_local_obs = mydata.mse_local_obs
rmse_local_obs = mydata.rmse_local_obs
x_test_local = mydata.x_test_local
x_test_global = mydata.x_test_global
covar_global = mydata.covar_global
covar_trace = mydata.covar_trace
covar_totelements = mydata.covar_totelements
covar_nonzeroelements = mydata.covar_nonzeroelements
AIC = mydata.AIC
BIC = mydata.BIC
f2_H_local = mydata.f2_H_local
f2_H_global = mydata.f2_H_global